In [14]:
import numpy as np
from numpy.random import seed
seed(1)
import pyfftw
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
import time as tm
import os

### 🌀 Jacobi Poisson Solver (`fps`)

This function solves the **Poisson equation**:

$\nabla^2 \psi = -\omega$

on a 2D periodic grid using the **Jacobi iterative method**.

**Steps:**
1. Initialize `psi = 0` everywhere.
2. Iteratively update each grid point:
   $\psi_{i,j}^{new} =
   \frac{
   (\psi_{i+1,j}^{old} + \psi_{i-1,j}^{old}) \,\Delta y^2 +
   (\psi_{i,j+1}^{old} + \psi_{i,j-1}^{old}) \,\Delta x^2 -
   \omega_{i,j}\,\Delta x^2 \Delta y^2
   }{2(\Delta x^2 + \Delta y^2)}$
3. Apply **periodic boundary conditions** after each update.
4. Compute error between successive iterations:
   $e = \frac{\|\psi^{new} - \psi^{old}\|}{n_x n_y}$
5. Return the converged streamfunction ($\psi$).

⚠️ Note: Jacobi is simple but converges slowly. For large grids, FFT or Multigrid solvers are much faster.


In [15]:
def fps(nx, ny, dx, dy, w):
    """
    Simple Jacobi iterative solver for Poisson equation: ∇²ψ = -ω
    Periodic boundary conditions are enforced via bc().
    """
    tol=1e-6
    max_iter=10000
    psi = np.zeros_like(w)
    rhs = -w

    dx2, dy2 = dx*dx, dy*dy
    denom = 2.0*(dx2 + dy2)

    for it in range(max_iter):
        psi_old = psi.copy()

        psi[1:nx+2,1:ny+2] = ((psi_old[2:nx+3,1:ny+2] + psi_old[0:nx+1,1:ny+2]) * dy2 +
                              (psi_old[1:nx+2,2:ny+3] + psi_old[1:nx+2,0:ny+1]) * dx2 -
                              rhs[1:nx+2,1:ny+2] * dx2 * dy2) / denom

        psi = bc(nx, ny, psi)  # enforce periodicity

        # check convergence
        err = np.linalg.norm(psi - psi_old) / (nx*ny)
        if err < tol:
            break

    return psi


In [16]:
# -------------------------------
# Periodic boundary condition
# -------------------------------
def bc(nx,ny,u):
    u[:,0] = u[:,ny]
    u[:,ny+2] = u[:,2]
    u[0,:] = u[nx,:]
    u[nx+2,:] = u[2,:]
    return u

### ⚡ RHS of Vorticity Equation (`rhs`)

This function computes the **right-hand side** of the vorticity transport equation:

$$
\frac{\partial \omega}{\partial t} = -J(\psi,\omega) + \frac{1}{Re}\nabla^2 \omega
$$

where:

- $J(\psi,\omega)$ is the **Jacobian operator (advection)**:

$$
J(\psi,\omega)_{i,j} \approx
\left(\frac{\psi_{i+1,j} - \psi_{i-1,j}}{2\Delta x}\right)
\left(\frac{\omega_{i,j+1} - \omega_{i,j-1}}{2\Delta y}\right)
-
\left(\frac{\psi_{i,j+1} - \psi_{i,j-1}}{2\Delta y}\right)
\left(\frac{\omega_{i+1,j} - \omega_{i-1,j}}{2\Delta x}\right)
$$

- $\nabla^2 \omega$ is the **Laplacian (diffusion)**:

$$
\nabla^2 \omega_{i,j} \approx
\frac{\omega_{i+1,j} - 2\omega_{i,j} + \omega_{i-1,j}}{\Delta x^2}
+
\frac{\omega_{i,j+1} - 2\omega_{i,j} + \omega_{i,j-1}}{\Delta y^2}
$$

Thus, the discrete RHS at grid point $(i,j)$ is:

$$
f_{i,j} = -J(\psi,\omega)_{i,j} + \frac{1}{Re}\nabla^2 \omega_{i,j}
$$


In [17]:
def rhs(nx, ny, dx, dy, Re, w, s, x, y, t):
    """
    RHS using simple central differences for Jacobian
    """
    inv_dx = 1.0 / (2.0*dx)
    inv_dy = 1.0 / (2.0*dy)

    # central derivatives
    dpsi_dx = (s[2:nx+3,1:ny+2] - s[0:nx+1,1:ny+2]) * inv_dx
    dpsi_dy = (s[1:nx+2,2:ny+3] - s[1:nx+2,0:ny+1]) * inv_dy
    domega_dx = (w[2:nx+3,1:ny+2] - w[0:nx+1,1:ny+2]) * inv_dx
    domega_dy = (w[1:nx+2,2:ny+3] - w[1:nx+2,0:ny+1]) * inv_dy

    # Jacobian
    jac = dpsi_dx * domega_dy - dpsi_dy * domega_dx

    # Laplacian (diffusion)
    lap = ((w[2:nx+3,1:ny+2] - 2.0*w[1:nx+2,1:ny+2] + w[0:nx+1,1:ny+2]) / dx**2
         + (w[1:nx+2,2:ny+3] - 2.0*w[1:nx+2,1:ny+2] + w[1:nx+2,0:ny+1]) / dy**2)


    f = np.zeros_like(w)
    f[1:nx+2,1:ny+2] = -jac + lap/Re 
    return f


### 🌪 Initial Condition: Vortex Merger (`vm_ic`)

The initial vorticity field is defined as the **superposition of two Gaussian vortices**:

$$
\omega(x,y) =
\exp\!\Big(-\sigma \big[(x-x_{c1})^2 + (y-y_{c1})^2\big]\Big)
+
\exp\!\Big(-\sigma \big[(x-x_{c2})^2 + (y-y_{c2})^2\big]\Big)
$$

with parameters:

- $\sigma = \pi$ (controls vortex size / spread),
- First vortex center: $(x_{c1}, y_{c1}) = \left(\pi - \tfrac{\pi}{4}, \pi\right)$,
- Second vortex center: $(x_{c2}, y_{c2}) = \left(\pi + \tfrac{\pi}{4}, \pi\right)$.

This produces two equal vortices located symmetrically about the vertical centerline.  
The `bc()` function is then used to enforce **periodic boundary conditions** on the domain.


In [18]:
# -------------------------------
# Initial condition (vortex merger)
# -------------------------------
def vm_ic(nx,ny,x,y):
    w = np.empty((nx+3,ny+3))
    sigma = np.pi
    xc1, yc1 = np.pi-np.pi/4.0, np.pi
    xc2, yc2 = np.pi+np.pi/4.0, np.pi
    w[1:nx+2, 1:ny+2] = np.exp(-sigma*((x[0:nx+1, 0:ny+1]-xc1)**2 + (y[0:nx+1, 0:ny+1]-yc1)**2)) \
                       + np.exp(-sigma*((x[0:nx+1, 0:ny+1]-xc2)**2 + (y[0:nx+1, 0:ny+1]-yc2)**2))
    return bc(nx,ny,w)

In [19]:
# -------------------------------
# Simulation parameters
# -------------------------------
nd = 128
nt = 3000
re = 560.0
dt = 0.01
save_freq = 20

nx, ny = nd, nd
lx, ly = 2.0*np.pi, 2.0*np.pi
dx, dy = lx/nx, ly/ny
x, y = np.meshgrid(np.linspace(0.0,2.0*np.pi,nx+1),
                   np.linspace(0.0,2.0*np.pi,ny+1), indexing='ij')

# -------------------------------
# Initialization
# -------------------------------
w = vm_ic(nx,ny,x,y)
s = fps(nx, ny, dx, dy, -w); s = bc(nx,ny,s)
t = np.empty_like(w)
r = np.empty_like(w)

snapshots = [np.copy(w)]
aa, bb = 1/3, 2/3

# -------------------------------
# Time stepping (RK3)
# -------------------------------
for k in range(1, nt+1):
    time = k*dt
    r = rhs(nx,ny,dx,dy,re,w,s,x,y,time)

    # stage 1
    t[1:nx+2,1:ny+2] = w[1:nx+2,1:ny+2] + dt*r[1:nx+2,1:ny+2]
    t = bc(nx,ny,t)
    s = fps(nx, ny, dx, dy, -t); s = bc(nx,ny,s)
    r = rhs(nx,ny,dx,dy,re,t,s,x,y,time)

    # stage 2
    t[1:nx+2,1:ny+2] = 0.75*w[1:nx+2,1:ny+2] + 0.25*t[1:nx+2,1:ny+2] + 0.25*dt*r[1:nx+2,1:ny+2]
    t = bc(nx,ny,t)
    s = fps(nx, ny, dx, dy, -t); s = bc(nx,ny,s)
    r = rhs(nx,ny,dx,dy,re,t,s,x,y,time)

    # stage 3
    w[1:nx+2,1:ny+2] = aa*w[1:nx+2,1:ny+2] + bb*t[1:nx+2,1:ny+2] + bb*dt*r[1:nx+2,1:ny+2]
    w = bc(nx,ny,w)
    s = fps(nx, ny, dx, dy, -w); s = bc(nx,ny,s)

    if k % save_freq == 0:
        snapshots.append(np.copy(w))

In [20]:
# -------------------------------
# Animation
# -------------------------------
fig, ax = plt.subplots(figsize=(6,6))
cmap = 'jet'

def animate(i):
    ax.clear()
    cs = ax.contourf(snapshots[i][1:nx+2,1:ny+2].T, 80, cmap=cmap)
    ax.set_title(f"Step {i*save_freq}, t={i*save_freq*dt:.2f}")
    return cs

ani = animation.FuncAnimation(fig, animate, frames=len(snapshots), interval=100, blit=False)
plt.close(fig)
# Show inline in Jupyter
display(HTML(ani.to_jshtml()))

Do you observe any vortex merger ? What happened ? 